# Pub/Sub Simulated Click Stream

## Make up a random Click event. 

In [ ]:
import json
import time
import random
from datetime import datetime

# Arrays of usernames and products
usernames = [
    "tech_savvy", "gamer123", "pc_builder", "keyboard_warrior", "mouse_master", "laptop_lover",
    "coder_jane", "geek_guy", "hardware_harry", "pc_pro", "desktop_dude", "monitor_maven",
    "peripheral_queen", "it_guru", "ssd_speedster", "ram_rocker", "techie_tom", "gadget_girl",
    "gpu_guru", "motherboard_mike", "keyboard_king", "tech_traveler", "screen_savvy", "build_master",
    "device_diva"
]

products = [
    {"id": "P001", "name": "Gaming Laptop"}, {"id": "P002", "name": "Mechanical Keyboard"},
    {"id": "P003", "name": "Wireless Mouse"}, {"id": "P004", "name": "4K Monitor"},
    {"id": "P005", "name": "Gaming Chair"}, {"id": "P006", "name": "Graphics Card"},
    {"id": "P007", "name": "External SSD"}, {"id": "P008", "name": "Desktop PC"},
    {"id": "P009", "name": "Laptop Stand"}, {"id": "P010", "name": "USB-C Hub"},
    {"id": "P011", "name": "Noise Cancelling Headphones"}, {"id": "P012", "name": "Gaming Mouse Pad"},
    {"id": "P013", "name": "Webcam"}, {"id": "P014", "name": "Bluetooth Speakers"},
    {"id": "P015", "name": "VR Headset"}, {"id": "P016", "name": "CPU Cooler"},
    {"id": "P017", "name": "RAM Kit"}, {"id": "P018", "name": "Power Supply Unit"},
    {"id": "P019", "name": "Motherboard"}, {"id": "P020", "name": "Portable Hard Drive"},
    {"id": "P021", "name": "Surge Protector"}, {"id": "P022", "name": "Ethernet Cable"},
    {"id": "P023", "name": "Laptop Bag"}, {"id": "P024", "name": "Smartphone Holder"},
    {"id": "P025", "name": "USB Flash Drive"}
]

# Function to generate random click data
def generate_click_data():
    username = random.choice(usernames)
    route = random.choice(['/home', '/about', '/contact', '/products', '/cart'])
    parameters = []
    
    # Add a product if the route is /products
    if route == '/products':
        product = random.choice(products)
        parameters.append({"name": "product_id", "value": product["id"]})
        parameters.append({"name": "product_name", "value": product["name"]})
        
        
    if route == '/cart':
        product = random.choice(products)
        parameters.append({"name": "product_id", "value": product["id"]})
        parameters.append({"name": "product_name", "value": product["name"]})
        parameters.append({"name": "quantity", "value": str(random.randint(1, 3))})
    
    
    # Set the method based on the route
    if route == '/cart':
        method = 'POST'
    else:
        method = 'GET'
    
    click_data = {
        'timestamp': datetime.utcnow().isoformat() + 'Z',
        'username': username,
        'route': route,
        'method': method,
        'parameters': parameters
    }
    return click_data


print("Done")

## Print some example click events

In [ ]:
# Call the generate_click_data function 50 times and print the results
for _ in range(50):
    click_data = generate_click_data()
    if click_data["method"] == "POST":
        print(click_data)


# Send a Click event to Pub/Sub

In [ ]:
from google.cloud import pubsub_v1

# Example usage
project_id = 'dsl-dar'
topic_id = 'clicks'

def publish_click_data(project_id, topic_id):
    publisher = pubsub_v1.PublisherClient()
    topic_path = publisher.topic_path(project_id, topic_id)

    click_data = generate_click_data()
    data_str = json.dumps(click_data)
    data_bytes = data_str.encode('utf-8')

    future = publisher.publish(topic_path, data_bytes)
    print(f'Published message ID: {future.result()}')


# Send a message

In [ ]:
# Call the publish_click_data function
publish_click_data(project_id, topic_id)

# Send some number of messages for a specified duration. 

In [ ]:
times_per_minute = 120
duration_minutes = 10 # Specify the duration in minutes
interval = 60 / times_per_minute

# Loop to call the publish_click_data function a specified number of times per minute for a specified duration
end_time = time.time() + duration_minutes * 60
count = 0
while time.time() < end_time:
    for _ in range(times_per_minute):
        publish_click_data(project_id, topic_id)
        count = count + 1
        time.sleep(interval)

print("Done")
print(count)